# Thinkful Capstone Project: "Etsy Epiphany"
### By Tiani Calip

# Problem Addressed

## Personal Interest and Problem
My mom owns an Etsy online store and is constantly stressing out about how well her products are doing, what price she should be listing her products at, and what product she should make and sell next. I want to create a solution for her to be able to identify what the most popular products are, how the reviews trend over time, and how the sentiment of review text maps against the review ratings. This way, she would be able to see how her products are doing compared to similar items on Etsy, and be able to respond to the demand for certain types of popular items and create and sell her own. Sometimes, she doesn’t understand why one shirt sells more than another. Providing review mapping and sentiment analysis will allow her and other users to identify what qualities of their products are favorable or not, be able to address those during production, and thereby possibly increase their chance of getting favorited.  

## Hypothesis  
Using NLP and machine learning techniques, I can identify the top 10 important qualities and price range needed for any given Etsy user to use to improve their chance of getting favorited.  

### Gameplan:   
Get the shop info for every shop that can be found with the keyword: "Disney"  
Use shop_ids to get the listing info   
Use the value of the feedback to train a classification model to know when a sentiment is positive or negative  
Identify the most important digrams/phrases in a shop's collective messages that lead to a positive sentiment  
Compare prices of the listings that have those positive sentiments  
Compare # of favorites to price of the listings with the positive sentiments  
Ccompare that with my mom's sentiments and prices and give suggestions for price and product qualities

have barplot
top summary words printed on top of the bars that lead to what rating it has
pos/neg sentiments. what ppl value? what needs improvement
Break down by shop  
avg rating per shop (btwn 0 and 1)  
page rank thing. summary for diff shops.  
nlp on description or tags of the listings  
fork out positive reviews and negative. see what ppl are saying abt both, give advice to the stores for what they could change abt their stores and improve.  
give suggestions abt what shop can do that others/competetors are doing  


## Impact  
I can determine the important qualities of a product that lead to the best reviews and review sentiments, then identify the most optimal price to sell the product. This can help my mom and any other prospective users to get ideas for their next products, and have confidence to list the products at an optimal price for both the seller and the buyer.  

# Dataset  
Data source = Etsy itself! I used the Etsy API to collect the data in real time from members of my mom's "circle", who sell and buy products similar to hers.  

## Existing Efforts
No existing Etsy apps look at both review scores and sentiments in an effort to identofy important qualities. I'm excited to see if I can be the first!  

# Project Concerns


## Assumptions
I am making the assumption that the limits and offset that I chose will give me a good representation of the Disney themed Etsy store population

## Risks (of data or models)
This is my first time using an API outside of the Thinkful course. I do not expect it to be an easy learning curve.  
Some data that would be ideal requires an OAuthentification, which means any user I want to scrape data from needs to verify and approve my data scraping. I do not want random users to feel threatened by my data grabbing, so I will have to go in a roundabout way to grab the data I want.  

## Questions Resulting
What is the best way to measure my scenario (binary outcome, probability outcome, or quantitative outcome)?


# Outcomes
To finish later

## Future work:
Look at the number of sales of those listings 
Compare sales to price of the listings with the positive sentiments

In [1]:
# Import packages needed
import pandas as pd
import numpy as np
import requests
import re
import json
import time
import csv
import lxml

In [ ]:
# Find shops w/ keyword "Disney", limit to first 200 shops
# Tells me which shops sell Disney themed items
disney_shops_results = []
disney_shops_results.append(json.loads(requests.get(
    'https://openapi.etsy.com/v2/shops?shop_name=Disney&limit=50&offset=0&api_key=j6ws81elytduo5sqhdm5egqv').text)['results'])
disney_shops_results.append(json.loads(requests.get(
    'https://openapi.etsy.com/v2/shops?shop_name=Disney&limit=50&offset=50&api_key=j6ws81elytduo5sqhdm5egqv').text)['results'])
disney_shops_results.append(json.loads(requests.get(
    'https://openapi.etsy.com/v2/shops?shop_name=Disney&limit=50&offset=100&api_key=j6ws81elytduo5sqhdm5egqv').text)['results'])
disney_shops_results.append(json.loads(requests.get(
    'https://openapi.etsy.com/v2/shops?shop_name=Disney&limit=50&offset=150&api_key=j6ws81elytduo5sqhdm5egqv').text)['results'])

In [13]:
# Display results of API request
# There's more info than we need
disney_shops_results

[[{'shop_id': 5001407,
   'shop_name': 'DisneyObscura',
   'user_id': 20413,
   'creation_tsz': 1139103736,
   'title': 'Obscure, rare, odd, vintage Disney memories on canvas.',
   'announcement': 'Spreading the love of Disney movies and Disneyland attractions through art.  Stills from your favorite movies, recreations of event and attraction posters and more to come.  *Custom Requests are Welcome!*  \nRight now these are all one of a kind, painted canvas pictures.  In the future, I may add prints and posters and I&#39;m working on wood cutouts and more.  &quot;Favorite&quot; my store and get updates as items are listed.   Thanks!',
   'currency_code': 'USD',
   'is_vacation': False,
   'vacation_message': None,
   'sale_message': 'Thank you for your purchase!  Your item will be wrapped and custom boxed and sent via USPS priority mail with tracking and insurance in the U.S. and first class international everywhere else.     Since this is artwork, it is non-refundable/no returns.  If it

In [17]:
# Make a data frame for the Disney shops and save it
disney_shopssdf = pd.DataFrame()
for results in disney_shops_results:
    if len(results) > 0:
        # Grab only the information that's useful to me
        df = pd.DataFrame(data=results)[
            ['user_id', 'login_name', 'shop_name', 'shop_id', 'listing_active_count', 'url']]
        # Put all the info in one large data frame
        disney_shopssdf = disney_shopssdf.append(df)
# Save the info for future use
disney_shopssdf.to_csv('disney_shopssdf.csv', index=False)

In [20]:
disney_shopssdf = pd.read_csv('disney_shopssdf.csv')
disney_shopssdf

user_id           login_name             shop_name   shop_id  \
0        20413      shamanicvisions         DisneyObscura   5001407   
1     30837077         marywinkler5          DisneyforFUN   7867596   
2     24112050     charliemarieriri          LittleWallop   8159392   
3     38103717     disneynerdclique      DisneyNerdClique   8632402   
4     20850951      sharkattack2878  MakingCruiseMemories   8635548   
5     44053694  disneyfreakboutique   DisneyFreakBoutique   9140037   
6     44647121        kdorlamarquis  Disneykenscollection   9188796   
7     42828296              nuhertz              RetroCot   9524912   
8      6112479           jenstar519      DisneyBottleCaps   9544253   
9     33819301          jenndukes06   DisneypassionJennie   9881742   
10    27992879        elliemcguire1  DisneyCollectorPlate  10850759   
11    75643457         sallyahmadi1  SallysEnchantingEars  11973795   
12    43098919          heatherly95     MagicalCreationCo  12282791   
13    18713976          natalilyuta     NataliFashionDOLL  12385533   
14    45547944            mermaidci   imaginaryearsbycici  12484473   
15    37407286           dianavero8           OhLittleMia  12485057   
16    82117396         itsladypluto        DesignsbyAnika  12530849   
17    41754016            mjbimonte     InvitationDISigns  12582429   
18    83192767    GreenEyedBlonde15         BlondeEmerald  12647065   
19    46077024            ingride14            DisneyBead  12912020   
20    57073011      shannoncurran85       DreamLikeWaltco  13697477   
21    80389978   catherine65thomson           Disney1ears  13787063   
22    98732819        EtsyDisneyDad           DisneyDad29  13817791   
23   103655661        blondeautumn9          Disneyautumn  14483493   
24   102570160         disneydapper          DisneyDapper  14506382   
25   104542970        DisneyCruisin         DisneyCruisin  14715524   
26   109927775         disneybreeze          DisneyBreeze  14839004   
27   111775326       olivialattanza  DisneyWishesByOlivia  15384940   
28   120126609             thll7ms0             Nicesales  15684246   
29   118332096             fpwgruft          DisneyBlisse  15861790   
..         ...                  ...                   ...       ...   
170  166499240    DisneyDazeForDays     DisneyDazeForDays  18311448   
171  100750624            keriscutt       DisneyBathMagic  14292089   
172  132735172             zi16ech6   DisneyDreamingFinds  16662955   
173   59065948        Hannahbell469        StampedStudios  10669757   
174  132014769         duynguyen866          TigerDArtist  16490429   
175   20986912         stupidgirl18    disneyaddictedears  12421289   
176   29027458          DisneyToYou           DisneyToYou   7675268   
177  165707232             qvhuq0w3   DisneydreamsByKelly  18280447   
178   62675363           sqwishymoe          DisneyGirl44  15448883   
179   58117265          haliecat926      DisneyEverything  13128577   
180  146240552             ihkr0vpj       Disneyholic1985  17406756   
181  126889264             zkgrgeow   DisneyNStuffByHaley  16592285   
182   99330765          kaitlyndk02   DisneyEnchantedEars  18402104   
183  108358087       kayleighcook17      DisneybyKayleigh  14680466   
184   22706378          trangpham36          KnotaBigDeal  10140698   
185   40617235          adisney1409        DisneyDesignCo  12936863   
186   37473468              mom2tkm  MyFairytaleCreations  10323286   
187  118541368             nycqx5m7            Disneydayz  16288110   
188   88138992      carberyjennifer      DisneyGliderTrio  15948266   
189   93739476            xFlareonx    DisneyMysteryBoxes  18358473   
190   67397551           cocolove77        DisneysArtShop  15082254   
191   36975495            ummemilie     DisneyDIYBoutique  17400511   
192   48995116          ellenmary67   Disney4shorejewelry   9759580   
193  106376342           njanowski1     DisneyyslimezShop  17141261   
194  158111986             3jyl

In [5]:
# Automate the ways I grab listing and user info after knowing the shop info
id_list = disney_shopssdf[['user_id', 'shop_id']]
user_id_list = id_list['user_id'].tolist()
shop_id_list = id_list['shop_id'].tolist()

In [22]:
# List of listings
# Some shops have over 1000 listings. I have chosen the offsets randomly after the first 300
find_listings_results = []
for shops in shop_id_list:
    base_url = 'https://openapi.etsy.com/v2/shops/' + \
        str(shops) + '/listings/active?sort_on=score&limit=100&offset=0&api_key=j6ws81elytduo5sqhdm5egqv'
    url_next = 'https://openapi.etsy.com/v2/shops/' + \
        str(shops) + '/listings/active?sort_on=score&limit=100&offset=100&api_key=j6ws81elytduo5sqhdm5egqv'
    next_url = 'https://openapi.etsy.com/v2/shops/' + \
        str(shops) + '/listings/active?sort_on=score&limit=100&offset=200&api_key=j6ws81elytduo5sqhdm5egqv'
    url_mid = 'https://openapi.etsy.com/v2/shops/' + \
        str(shops) + '/listings/active?sort_on=score&limit=100&offset=500&api_key=j6ws81elytduo5sqhdm5egqv'
    url_last = 'https://openapi.etsy.com/v2/shops/' + \
        str(shops) + '/listings/active?sort_on=score&limit=100&offset=900&api_key=j6ws81elytduo5sqhdm5egqv'
    find_listings_results.append(json.loads(
        requests.get(base_url).text)['results'])
    find_listings_results.append(json.loads(
        requests.get(url_next).text)['results'])
    find_listings_results.append(json.loads(
        requests.get(next_url).text)['results'])
    find_listings_results.append(json.loads(
        requests.get(url_mid).text)['results'])
    find_listings_results.append(json.loads(
        requests.get(url_last).text)['results'])

In [ ]:
# Visualize the request results
# Again, there's more info than I need
find_listings_results

In [24]:
# Make a data frame for the Disney shops' listings and save it
listings_df = pd.DataFrame()
for results in find_listings_results:
    if len(results) > 0:
        # Take only the info I want
        df = pd.DataFrame(data=results)[['user_id', 'listing_id', 'title', 'description',
                                         'tags', 'style', 'is_digital', 'is_customizable', 'price', 'url']]
        listings_df = listings_df.append(df)
listings_df

listings_df.to_csv('dis_shop_listings_df.csv', index=False)

user_id  listing_id                                              title  \
0       20413   492259062  Moana toddler baby with Stitch crossover mashu...   
1       20413   464863490  Lilo and Stitch with Scrump and Pleakly.  9 x ...   
2       20413   243657597  Custom Disney or Pixar themed painting, your c...   
3       20413   625330096  Disney&#39;s Lilo and Stitch - Fat man and Sti...   
4       20413   639116667  Queen Grimhilde magic mirror Snow White, Yzma ...   
5       20413   625280804  Maleficent Sleeping Beauty, ravens and, Queen ...   
6       20413   639107951  Stitch and Queen Grimhilde Evil Wicked Hag Sno...   
7       20413   243521750  Tipo and Chaca from the classic and funny Disn...   
8       20413   243518492  Be nice to Mermaids!  Ariel, the Little Mermai...   
9       20413   241680506  Maleficent and Diablo from Disney&#39;s Sleepi...   
10      20413   257552659  Blowing Bubbles After The Bath. Dumbo the Elep...   
11      20413   238573318  Yzma talking eyeball from Disney&#39;s The Emp...   
12      20413   238581690  Hercules VS The Lightning Bolt Disney&#39;s cu...   
13      20413   238571522  Absolutely insane scene from Disney&#39;s Herc...   
14      20413   238569476  White Kitten from The Princess And The Frog.  ...   
15      20413   238470269  White Kitten from The Princess And The Frog. D...   
16      20413   238449117  Full Set Classic Toot Whistle Plunk and Boom -...   
17      20413   481091347  Unique Song Of The South Brer Rabbit. Titled; ...   
0    30837077   530216099  Disney character or Disney cruise line water b...   
1    30837077   464207368         4 Disney Cruise Magnets for stateroom door   
2    30837077   492512510  Customized DCL Disney cruise line tumblers cup...   
3    30837077   261630013  Little mermaid disney wedding theme ariel ears...   
4    30837077   233408848         4 Disney Cruise Magnets for stateroom door   
5    30837077   222447256  Disney Wedding bride tshirt or tanktop any tsh...   
6    30837077   219269069  Customized DCL Disney cruise line tumblers cup...   
7    30837077   213871085                     Personalized Vinyl 25 of them    
8    30837077   205732377  Customized DCL Disney cruise line tumblers cup...   
9    30837077   211971680                     Personalized Vinyl 25 of them    
10   30837077   208433425  10 DCL Disney Mickey Mouse bottle cap Key Chai...   
11   30837077   197510986  Disney trip or disney cruise dcl wine tumbler ...   
..        ...         ...                                                ...   
3    48995116   547288960                      Adjustable sea glass bracelet   
4    48995116   547288344                                     Charming Laces   
5    48995116   547287916                     Round screw ends bead bracelet   
0   106376342   598110981                                         Snow White   
0   158111986   608640156             Personalized Key to the Disney Kingdom   
1   158111986   621139667                          Key to the Disney Kingdom   
0   160854822   637172449     SOLD******* LED Light-Up Christmas Disney Ears   
1   160854822   637171641          SOLD********* Plush Lion King Disney Ears   
2   160854822   626548409  Sun Flower/Flower Child Disney Ears! **just ad...   
3   160854822   626543255                  Moana/Tropical Floral Disney Ears   
0   110167835   607935915                      Seahawks Inspired Flower Ears   
0   104547525   626788971                              Signature Disney Ears   
1   104547525   612953228                         Animal Kingdom Disney Ears   
2   104547525   612950850                           Up Up & Away Disney Ears   
3   104547525   612949472                                   Rose Disney Ears   
4   104547525   612945688                        Furry Chewbacca Disney Ears   
5   104547525   612943892                      Starry Night Time Disney Ears   
6   104547525   612953922                          Under the Sea Disney Ears   
0   14

In [10]:
# Automate the ways I can grab review info after knowing the user_ids
# Grabbing the first 300 reviews of each user
find_reviews_results = []
for users in user_id_list:
    base_url = 'https://openapi.etsy.com/v2/users/' + \
        str(users) + '/feedback/as-seller?limit=100&offset=0&api_key=j6ws81elytduo5sqhdm5egqv'
    next_url = 'https://openapi.etsy.com/v2/users/' + \
        str(users) + '/feedback/as-seller?limit=100&offset=100&api_key=j6ws81elytduo5sqhdm5egqv'
    url_next = 'https://openapi.etsy.com/v2/users/' + \
        str(users) + '/feedback/as-seller?limit=100&offset=200&api_key=j6ws81elytduo5sqhdm5egqv'
    last_url = 'https://openapi.etsy.com/v2/users/' + \
        str(users) + '/feedback/as-seller?limit=100&offset=300&api_key=j6ws81elytduo5sqhdm5egqv'
    find_reviews_results.append(json.loads(
        requests.get(base_url).text)['results'])
    find_reviews_results.append(json.loads(
        requests.get(next_url).text)['results'])
    find_reviews_results.append(json.loads(
        requests.get(url_next).text)['results'])
    find_reviews_results.append(json.loads(
        requests.get(last_url).text)['results'])
find_reviews_results

[[{'feedback_id': 321233074,
   'creation_tsz': 1536893841,
   'message': 'if i could give this 1,000 stars i would!! i love this piece so much!! such a wonderful piece of artwork to add to my collection, and also a wonderful and talented artist!! i will DEFINITELY be buying more artwork!! thank you so much, it means the world to me✨',
   'value': 1,
   'seller_user_id': 20413,
   'transaction_id': 1486272007,
   'image_feedback_id': None,
   'image_url_25x25': 'https://www.etsy.com/images/grey.gif',
   'image_url_155x125': 'https://www.etsy.com/images/grey.gif',
   'image_url_fullxfull': 'https://www.etsy.com/images/grey.gif',
   'target_user_id': 20413},
  {'feedback_id': 319990968,
   'creation_tsz': 1535326403,
   'message': 'You CANNOT go wrong with ordering from this shop!  She is great, prompt, and does fantastic custom work.  I will be back again for sure! ',
   'value': 1,
   'seller_user_id': 20413,
   'transaction_id': 1466696489,
   'image_feedback_id': None,
   'image_url_

In [11]:
# Make a data frame with the Disney shops' reviews and save it
reviewsdf = pd.DataFrame()
for results in find_reviews_results:
    if len(results) > 0:
        # Grab only the info that's useful
        df = pd.DataFrame(data=results)[
            ['feedback_id', 'seller_user_id', 'message', 'value']]
        reviewsdf = reviewsdf.append(df)
# Rename so I can merge all the data frames on user_id
reviewsdf = reviewsdf.rename(index=str, columns={"seller_user_id": "user_id"})
reviewsdf

feedback_id    user_id                                            message  \
0   321233074.0      20413  if i could give this 1,000 stars i would!! i l...   
1   319990968.0      20413  You CANNOT go wrong with ordering from this sh...   
2   314893601.0      20413  Rhonda! You are truly a magical woman! You bri...   
3   314226292.0      20413  Absolutely in love! They&#39;re exactly what I...   
4   308755577.0      20413  I love it! I like that she made it her own by ...   
5   302109457.0      20413  Came back to commission this next painting for...   
6   301569979.0      20413                     Rhonda is a great find on Etsu   
7   301473094.0      20413  Second time coming to Rhonda for a purchase.  ...   
8   295495440.0      20413  Absolutely a masterpiece. The best painting I ...   
9   292736232.0      20413  This is a masterpiece that belongs at Disneyla...   
10  288215630.0      20413  Could not have asked for a better product. Mat...   
11  285651217.0      20413                                       Looks great!   
12  285290754.0      20413  It turned out perfect. My entire team thinks i...   
13  276102127.0      20413                            It was perfect! Love it   
14  275684806.0      20413                     So beautiful! Thanks again! :)   
15  273051762.0      20413  I don&#39;t think I&#39;ve ever received somet...   
16  272483689.0      20413  Gorgeous painting, fantastic customer service ...   
17  271030637.0      20413  I received the painting today and my daughter ...   
18  260463362.0      20413         Super cool and unique gift, fast shipping.   
19  257522128.0      20413                                               None   
20  254916721.0      20413  Absolutely adorable. Super fast shipping. Thanks!   
21  254826751.0      20413  A very stunning piece of art. My son loved it ...   
22  254844380.0      20413  It is amazingly perfect! A beautiful piece of ...   
23  254062726.0      20413  I loved this painting when I saw it, but it is...   
24  253158434.0      20413  So good it was supposed to be a gift and I kep...   
25  252569524.0      20413  The item came on time and it&#39;s beautiful! ...   
26  247619333.0      20413  Very fast with shipping, the owner is very nic...   
27  246778363.0      20413  Most interesting addition to my pop art collec...   
28  243754384.0      20413  Lovely! Great colors and detail.  Fast shippin...   
29  242814561.0      20413  Love love love the picture.  My daughter loves...   
..          ...        ...                                                ...   
4   220062297.0   37473468  Ordered this as a gift for a friend and it was...   
0   320667241.0   88138992  Love loved loved the cage set. Thanks so much ...   
1   319376295.0   88138992                       It was excatly as described.   
2   314217384.0   88138992  Wow! This cage set is so great and the shop ow...   
3   314200009.0   88138992  Cute little bag with very fast shipping! It is...   
4   312708090.0   88138992  Very well made and it looks like it will wash ...   
5   312276335.0   88138992                                               None   
6   310183141.0   88138992  I recieved a custom order from DisneyGliderTri...   
7   308572082.0   88138992  Great cage set! Jennifer is awesome! Quick to ...   
8   307359110.0   88138992                                               None   
9   306713878.0   88138992                                               None   
10  304029443.0   88138992  I ordered 2 sets absolutely adorable so I orde...   
11  303613161.0   88138992                                               None   
12  302724725.0   88138992  It’s perfect! Seller has excellent communicati...   
13  302087699.0   88138992                                               None   
14  301346310.0   88138992                               Super fast shipping!   
15  300387357.0   88138992  Love this cage set! And so does my little Pipp...   
16  298951186.0   88138992         

In [12]:
# Save for future use
reviewsdf.to_csv('dis_shop_reviewsdf.csv', index=False)

In [2]:
# Open all the csv files containing the data frames from my Etsy API requests
disney_shopssdf = pd.read_csv('disney_shopssdf.csv')
dis_shop_reviewsdf = pd.read_csv('dis_shop_reviewsdf.csv')
dis_shop_reviewsdf = dis_shop_reviewsdf.rename(
    index=str, columns={"seller_user_id": "user_id"})
dis_shop_listings_df = pd.read_csv('dis_shop_listings_df.csv')

In [3]:
dis_shop_listings_df['listing_id'].unique().shape

(7070,)

In [4]:
listingid_list = dis_shop_listings_df[['listing_id']]

In [5]:
listingid_list = listingid_list['listing_id'].tolist()

In [ ]:
import pickle
find_favorites_results = []
# check all if it works, then grab everything I can before getting locked out again
for listings in listingid_list[0:3000]:
    # save r_save to disk using pickle
    base_url = 'https://openapi.etsy.com/v2/listings/' + \
        str(listings) + '/favored-by?limit=100&api_key=j6ws81elytduo5sqhdm5egqv'
    if listings is not None:
        try:
            r = requests.get(base_url, timeout=3)
            r.raise_for_status()
            r_save = find_favorites_results.append(
                json.loads(r.text)['results'])
        except requests.exceptions.RequestException as err:
            print("OOps: Something Else", err)
        except requests.exceptions.HTTPError as errh:
            print("Http Error:", errh)
        except requests.exceptions.ConnectionError as errc:
            print("Error Connecting:", errc)
        except requests.exceptions.Timeout as errt:
            print("Timeout Error:", errt)
        print(requests.get(base_url).text)
find_favorites_results

In [ ]:
# Make a data frame with the Disney shops' reviews and save it
fav_df = pd.DataFrame()
for results in find_favorites_results:
    # Grab only the info that's useful
    if (results != Ellipsis):
        if len(results) > 0:
            df = pd.DataFrame(data=results)[['listing_id']]
            fav_df = fav_df.append(df)
fav_df

In [ ]:
pickle.dump(find_favorites_results, open("1find_favorites_results.pkl", "wb"))
fav_num = pd.DataFrame(fav_df['listing_id'].value_counts()).reset_index(
).rename(columns={'index': 'listing_id', 'listing_id': 'num_favorites'})
fav_num

In [ ]:
find_favorites_results2 = []
# check all if it works, then grab everything I can before getting locked out again
for listings in listingid_list[2645:4000]:
    # save r_save to disk using pickle
    base_url = 'https://openapi.etsy.com/v2/listings/' + \
        str(listings) + '/favored-by?limit=100&api_key=j6ws81elytduo5sqhdm5egqv'
    if listings is not None:
        try:
            r = requests.get(base_url, timeout=3)
            r.raise_for_status()
            r_save = find_favorites_results2.append(
                json.loads(r.text)['results'])
        except requests.exceptions.RequestException as err:
            print("OOps: Something Else", err)
        except requests.exceptions.HTTPError as errh:
            print("Http Error:", errh)
        except requests.exceptions.ConnectionError as errc:
            print("Error Connecting:", errc)
        except requests.exceptions.Timeout as errt:
            print("Timeout Error:", errt)
        print(requests.get(base_url).text)
find_favorites_results2

In [ ]:
# Make a data frame with the Disney shops' reviews and save it
fav2_df = pd.DataFrame()
for results in find_favorites_results2:
    # Grab only the info that's useful
    if (results != Ellipsis):
        if len(results) > 0:
            df = pd.DataFrame(data=results)[['listing_id']]
            fav2_df = fav2_df.append(df)
fav2_df

In [ ]:
pickle.dump(find_favorites_results2, open("2find_favorites_results.pkl", "wb"))
fav_num2 = pd.DataFrame(fav2_df['listing_id'].value_counts()).reset_index(
).rename(columns={'index': 'listing_id', 'listing_id': 'num_favorites'})
fav_num2

In [ ]:
find_favorites_results3 = []
# check all if it works, then grab everything I can before getting locked out again
for listings in listingid_list[3759:5000]:
    # save r_save to disk using pickle
    base_url = 'https://openapi.etsy.com/v2/listings/' + \
        str(listings) + '/favored-by?limit=100&api_key=j6ws81elytduo5sqhdm5egqv'
    if listings is not None:
        try:
            r = requests.get(base_url, timeout=3)
            r.raise_for_status()
            r_save = find_favorites_results3.append(
                json.loads(r.text)['results'])
        except requests.exceptions.RequestException as err:
            print("OOps: Something Else", err)
        except requests.exceptions.HTTPError as errh:
            print("Http Error:", errh)
        except requests.exceptions.ConnectionError as errc:
            print("Error Connecting:", errc)
        except requests.exceptions.Timeout as errt:
            print("Timeout Error:", errt)
        print(requests.get(base_url).text)
find_favorites_results3

In [ ]:
# Make a data frame with the Disney shops' reviews and save it
fav3_df = pd.DataFrame()
for results in find_favorites_results3:
    # Grab only the info that's useful
    if (results != Ellipsis):
        if len(results) > 0:
            df = pd.DataFrame(data=results)[['listing_id']]
            fav3_df = fav3_df.append(df)
fav3_df

In [ ]:
pickle.dump(find_favorites_results3, open("3find_favorites_results.pkl", "wb"))
# fav_counts = fav_df.drop_duplicates().groupby('listing_id')['user_id'].agg('count').sort_values()
fav_num3 = pd.DataFrame(fav3_df['listing_id'].value_counts()).reset_index(
).rename(columns={'index': 'listing_id', 'listing_id': 'num_favorites'})
fav_num3

In [ ]:
num_favs_agg = fav_num.append(fav_num2).append(fav_num3).reset_index()
num_favs_agg.shape

In [ ]:
num_favs_agg.num_favorites.unique()

In [ ]:
find_favorites_results4 = []
# check all if it works, then grab everything I can before getting locked out again
for listings in listingid_list[3871:7070]:
    # save r_save to disk using pickle
    base_url = 'https://openapi.etsy.com/v2/listings/' + \
        str(listings) + '/favored-by?limit=100&api_key=j6ws81elytduo5sqhdm5egqv'
    if listings is not None:
        try:
            r = requests.get(base_url, timeout=3)
            r.raise_for_status()
            r_save = find_favorites_results4.append(
                json.loads(r.text)['results'])
        except requests.exceptions.RequestException as err:
            print("OOps: Something Else", err)
        except requests.exceptions.HTTPError as errh:
            print("Http Error:", errh)
        except requests.exceptions.ConnectionError as errc:
            print("Error Connecting:", errc)
        except requests.exceptions.Timeout as errt:
            print("Timeout Error:", errt)
        print(requests.get(base_url).text)
find_favorites_results4

In [ ]:
# Make a data frame with the Disney shops' reviews and save it
fav4_df = pd.DataFrame()
for results in find_favorites_results4:
    # Grab only the info that's useful
    if (results != Ellipsis):
        if len(results) > 0:
            df = pd.DataFrame(data=results)[['listing_id']]
            fav4_df = fav4_df.append(df)
fav4_df

In [ ]:
pickle.dump(find_favorites_results4, open("4find_favorites_results.pkl", "wb"))
fav_num4 = pd.DataFrame(fav4_df['listing_id'].value_counts()).reset_index(
).rename(columns={'index': 'listing_id', 'listing_id': 'num_favorites'})
fav_num4

In [ ]:
find_favorites_results5 = []
# check all if it works, then grab everything I can before getting locked out again
for listings in listingid_list[6463:7070]:
    # save r_save to disk using pickle
    base_url = 'https://openapi.etsy.com/v2/listings/' + \
        str(listings) + '/favored-by?limit=100&api_key=j6ws81elytduo5sqhdm5egqv'
    if listings is not None:
        try:
            r = requests.get(base_url, timeout=3)
            r.raise_for_status()
            r_save = find_favorites_results5.append(
                json.loads(r.text)['results'])
        except requests.exceptions.RequestException as err:
            print("OOps: Something Else", err)
        except requests.exceptions.HTTPError as errh:
            print("Http Error:", errh)
        except requests.exceptions.ConnectionError as errc:
            print("Error Connecting:", errc)
        except requests.exceptions.Timeout as errt:
            print("Timeout Error:", errt)
        print(requests.get(base_url).text)
find_favorites_results5

In [ ]:
# Make a data frame with the Disney shops' reviews and save it
fav5_df = pd.DataFrame()
for results in find_favorites_results5:
    # Grab only the info that's useful
    if (results != Ellipsis):
        if len(results) > 0:
            df = pd.DataFrame(data=results)[['listing_id']]
            fav5_df = fav5_df.append(df)
fav5_df

In [ ]:
pickle.dump(find_favorites_results5, open("5find_favorites_results.pkl", "wb"))
fav_num5 = pd.DataFrame(fav5_df['listing_id'].value_counts()).reset_index(
).rename(columns={'index': 'listing_id', 'listing_id': 'num_favorites'})
fav_num5

In [ ]:
num_favs_agg = num_favs_agg.append(fav_num4).append(fav_num5).reset_index()
num_favs_agg = num_favs_agg.drop(['index'], axis=1)
# Save for future use
num_favs_agg.to_csv('num_favs_agg.csv', index=False)

In [14]:
# Find shops w/ keyword "Disney", limit to first 200 shops
# Tells me which shops sell Disney themed items
disney_shops_results2 = []
for shops in shop_id_list:
    disney_shops_results2.append(json.loads(requests.get('https://openapi.etsy.com/v2/shops/' + str(
        shops) + '?api_key=j6ws81elytduo5sqhdm5egqv').text)['results'])

In [33]:
# Make a data frame for the Disney shops and save it
shops_df = pd.DataFrame()
for results in disney_shops_results2:
    if len(results) > 0:
        # Grab only the information that's useful to me
        df = pd.DataFrame(data=results)[['shop_name', 'creation_tsz']]
        # Put all the info in one large data frame
        shops_df = shops_df.append(df)
# Save the info for future use
shops_df.to_csv('df_creation_tsz.csv', index=False)

In [29]:
shops_df

shop_id  creation_tsz
0    5001407    1139103736
0    7867596    1361637742
0    8159392    1487173090
0    8632402    1386206132
0    8635548    1380657794
0    9140037    1391727344
0    9188796    1392850793
0    9524912    1403719734
0    9544253    1423070214
0    9881742    1410326469
0   10850759    1426197104
0   11973795    1447125079
0   12282791    1451852017
0   12385533    1522249270
0   12484473    1454536109
0   12485057    1455147477
0   12530849    1460137317
0   12582429    1456025318
0   12647065    1456969111
0   12912020    1461517269
0   13697477    1475260300
0   13787063    1475689303
0   13817791    1475933780
0   14483493    1485739533
0   14506382    1486811927
0   14715524    1488398142
0   14839004    1490539504
0   15384940    1497813447
0   15684246    1501436470
0   15861790    1505786268
..       ...           ...
0   18311448    1534475870
0   14292089    1483213544
0   16662955    1513357885
0   10669757    1423254766
0   16490429    1511569295
0   12421289    1453754312
0    7675268    1359504940
0   18280447    1533841994
0   15448883    1498710887
0   13128577    1464733908
0   17406756    1522304051
0   16592285    1512420784
0   18402104    1535684828
0   14680466    1487816071
0   10140698    1413593833
0   12936863    1461625469
0   10323286    1417016502
0   16288110    1529788270
0   15948266    1504848679
0   18358473    1534871421
0   15082254    1493685552
0   17400511    1523317943
0    9759580    1492101631
0   17141261    1520208196
0   17909142    1529026931
0   18046963    1530848495
0   17533401    1523842970
0   16395797    1531097294
0   17199172    1519802446
0   16577785    1517611905

[200 rows x 2 columns]

In [8]:
listingid_list

[492259062,
 464863490,
 243657597,
 625330096,
 639116667,
 625280804,
 639107951,
 243521750,
 243518492,
 241680506,
 257552659,
 238573318,
 238581690,
 238571522,
 238569476,
 238470269,
 238449117,
 481091347,
 530216099,
 464207368,
 492512510,
 261630013,
 233408848,
 222447256,
 219269069,
 213871085,
 205732377,
 211971680,
 208433425,
 197510986,
 192097631,
 190989701,
 185098834,
 173579404,
 168479651,
 166844099,
 165760844,
 159752064,
 127239188,
 622957748,
 530216389,
 166550223,
 262937042,
 262534383,
 262515260,
 247946992,
 247897297,
 232482513,
 227277775,
 201577923,
 199767948,
 191694443,
 191688310,
 597227331,
 523833978,
 124489363,
 607297491,
 479014279,
 465524962,
 605454684,
 544869120,
 153161447,
 484665653,
 487042304,
 530107741,
 217175777,
 528942794,
 644621259,
 516710548,
 195160116,
 517166197,
 494727201,
 175345148,
 232052195,
 272438372,
 235806762,
 504140221,
 629918364,
 246638373,
 541076780,
 199080489,
 187185959,
 186292050,
 186

In [9]:
# Find listing info so I can know creation time
# Tells me which shops sell Disney themed items
listing_creation_results = []
for listings in listingid_list:
    r = requests.get('https://openapi.etsy.com/v2/listings/' +
                     str(listings) + '?api_key=j6ws81elytduo5sqhdm5egqv')
    print(listingid_list.index(listings))
    r_save = listing_creation_results.append(json.loads(r.text)['results'])

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

1861
1862
1863
1864
1865
1866
1867
1868
1869
1870
1871
1872
1873
1874
1875
1876
1877
1878
1879
1880
1881
1882
1883
1884
1885
1886
1887
1888
1889
1890
1891
1892
1893
1894
1895
1896
1897
1898
1899
1900
1901
1902
1903
1904
1905
1906
1907
1908
1909
1910
1911
1912
1913
1914
1915
1916
1917
1918
1919
1920
1921
1922
1923
1924
1925
1926
1927
1928
1929
1930
1931
1932
1933
1934
1935
1936
1937
1938
1939
1940
1941
1942
1943
1944
1945
1946
1947
1948
1949
1950
1951
1952
1953
1954
1955
1956
1957
1958
1959
1960
1961
1962
1963
1964
1965
1966
1967
1968
1969
1970
1971
1972
1973
1974
1975
1976
1977
1978
1979
1980
1981
1982
1983
1984
1985
1986
1987
1988
1989
1990
1991
1992
1993
1994
1995
1996
1997
1998
1999
2000
2001
2002
2003
2004
2005
2006
2007
2008
2009
2010
2011
2012
2013
2014
2015
2016
2017
2018
2019
2020
2021
2022
2023
2024
2025
2026
2027
2028
2029
2030
2031
2032
2033
2034
2035
2036
2037
2038
2039
2040
2041
2042
2043
2044
2045
2046
2047
2048
2049
2050
2051
2052
2053
2054
2055
2056
2057
2058
2059
2060


3500
3501
3502
3503
3504
3505
3506
3507
3508
3509
3510
3511
3512
3513
3514
3515
3516
3517
3518
3519
3520
3521
3522
3523
3524
3525
3526
3527
3528
3529
3530
3531
3532
3533
3534
3535
3536
3537
3538
3539
3540
3541
3542
3543
3544
3545
3546
3547
3548
3549
3550
3551
3552
3553
3554
3555
3556
3557
3558
3559
3560
3561
3562
3563
3564
3565
3566
3567
3568
3569
3570
3571
3572
3573
3574
3575
3576
3577
3578
3579
3580
3581
3582
3583
3584
3585
3586
3587
3588
3589
3590
3591
3592
3593
3594
3595
3596
3597
3598
3599
3600
3601
3602
3603
3604
3605
3606
3607
3608
3609
3610
3611
3612
3613
3614
3615
3616
3617
3618
3619
3620
3621
3622
3623
3624
3625
3626
3627
3628
3629
3630
3631
3632
3633
3634
3635
3636
3637
3638
3639
3640
3641
3642
3643
3644
3645
3646
3647
3648
3649
3650
3651
3652
3653
3654
3655
3656
3657
3658
3659
3660
3661
3662
3663
3664
3665
3666
3667
3668
3669
3670
3671
3672
3673
3674
3675
3676
3677
3678
3679
3680
3681
3682
3683
3684
3685
3686
3687
3688
3689
3690
3691
3692
3693
3694
3695
3696
3697
3698
3699


5139
5140
5141
5142
5143
5144
5145
5146
5147
5148
5149
5150
5151
5152
5153
5154
5155
5156
5157
5158
5159
5160
5161
5162
5163
5164
5165
5166
5167
5168
5169
5170
5171
5172
5173
5174
5175
5176
5177
5178
5179
5180
5181
5182
5183
5184
5185
5186
5187
5188
5189
5190
5191
5192
5193
5194
5195
5196
5197
5198
5199
5200
5201
5202
5203
5204
5205
5206
5207
5208
5209
5210
5211
5212
5213
5214
5215
5216
5217
5218
5219
5220
5221
5222
5223
5224
5225
5226
5227
5228
5229
5230
5231
5232
5233
5234
5235
5236
5237
5238
5239
5240
5241
5242
5243
5244
5245
5246
5247
5248
5249
5250
5251
5252
5253
5254
5255
5256
5257
5258
5259
5260
5261
5262
5263
5264
5265
5266
5267
5268
5269
5270
5271
5272
5273
5274
5275
5276
5277
5278
5279
5280
5281
5282
5283
5284
5285
5286
5287
5288
5289
5290
5291
5292
5293
5294
5295
5296
5297
5298
5299
5300
5301
5302
5303
5304
5305
5306
5307
5308
5309
5310
5311
5312
5313
5314
5315
5316
5317
5318
5319
5320
5321
5322
5323
5324
5325
5326
5327
5328
5329
5330
5331
5332
5333
5334
5335
5336
5337
5338


6778
6779
6780
6781
6782
6783
6784
6785
6786
6787
6788
6789
6790
6791
6792
6793
6794
6795
6796
6797
6798
6799
6800
6801
6802
6803
6804
6805
6806
6807
6808
6809
6810
6811
6812
6813
6814
6815
6816
6817
6818
6819
6820
6821
6822
6823
6824
6825
6826
6827
6828
6829
6830
6831
6832
6833
6834
6835
6836
6837
6838
6839
6840
6841
6842
6843
6844
6845
6846
6847
6848
6849
6850
6851
6852
6853
6854
6855
6856
6857
6858
6859
6860
6861
6862
6863
6864
6865
6866
6867
6868
6869
6870
6871
6872
6873
6874
6875
6876
6877
6878
6879
6880
6881
6882
6883
6884
6885
6886
6887
6888
6889
6890
6891
6892
6893
6894
6895
6896
6897
6898
6899
6900
6901
6902
6903
6904
6905
6906
6907
6908
6909
6910
6911
6912
6913
6914
6915
6916
6917
6918
6919
6920
6921
6922
6923
6924
6925
6926
6927
6928
6929
6930
6931
6932
6933
6934
6935
6936
6937
6938
6939
6940
6941
6942
6943
6944
6945
6946
6947
6948
6949
6950
6951
6952
6953
6954
6955
6956
6957
6958
6959
6960
6961
6962
6963
6964
6965
6966
6967
6968
6969
6970
6971
6972
6973
6974
6975
6976
6977


In [18]:
# Make a data frame for the Disney listing creation times, in epoch seconds and save it
listing_tsz_df = pd.DataFrame()
c = 0
for results in listing_creation_results:
    print(c)
    c = c+1
    if len(results) > 0:
        try:
            # Grab only the information that's useful to me
            df = pd.DataFrame(data=results)[['listing_id', 'creation_tsz']]
            # Put all the info in one large data frame
            listing_tsz_df = listing_tsz_df.append(df)
        except:
            pass

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

1898
1899
1900
1901
1902
1903
1904
1905
1906
1907
1908
1909
1910
1911
1912
1913
1914
1915
1916
1917
1918
1919
1920
1921
1922
1923
1924
1925
1926
1927
1928
1929
1930
1931
1932
1933
1934
1935
1936
1937
1938
1939
1940
1941
1942
1943
1944
1945
1946
1947
1948
1949
1950
1951
1952
1953
1954
1955
1956
1957
1958
1959
1960
1961
1962
1963
1964
1965
1966
1967
1968
1969
1970
1971
1972
1973
1974
1975
1976
1977
1978
1979
1980
1981
1982
1983
1984
1985
1986
1987
1988
1989
1990
1991
1992
1993
1994
1995
1996
1997
1998
1999
2000
2001
2002
2003
2004
2005
2006
2007
2008
2009
2010
2011
2012
2013
2014
2015
2016
2017
2018
2019
2020
2021
2022
2023
2024
2025
2026
2027
2028
2029
2030
2031
2032
2033
2034
2035
2036
2037
2038
2039
2040
2041
2042
2043
2044
2045
2046
2047
2048
2049
2050
2051
2052
2053
2054
2055
2056
2057
2058
2059
2060
2061
2062
2063
2064
2065
2066
2067
2068
2069
2070
2071
2072
2073
2074
2075
2076
2077
2078
2079
2080
2081
2082
2083
2084
2085
2086
2087
2088
2089
2090
2091
2092
2093
2094
2095
2096
2097


3557
3558
3559
3560
3561
3562
3563
3564
3565
3566
3567
3568
3569
3570
3571
3572
3573
3574
3575
3576
3577
3578
3579
3580
3581
3582
3583
3584
3585
3586
3587
3588
3589
3590
3591
3592
3593
3594
3595
3596
3597
3598
3599
3600
3601
3602
3603
3604
3605
3606
3607
3608
3609
3610
3611
3612
3613
3614
3615
3616
3617
3618
3619
3620
3621
3622
3623
3624
3625
3626
3627
3628
3629
3630
3631
3632
3633
3634
3635
3636
3637
3638
3639
3640
3641
3642
3643
3644
3645
3646
3647
3648
3649
3650
3651
3652
3653
3654
3655
3656
3657
3658
3659
3660
3661
3662
3663
3664
3665
3666
3667
3668
3669
3670
3671
3672
3673
3674
3675
3676
3677
3678
3679
3680
3681
3682
3683
3684
3685
3686
3687
3688
3689
3690
3691
3692
3693
3694
3695
3696
3697
3698
3699
3700
3701
3702
3703
3704
3705
3706
3707
3708
3709
3710
3711
3712
3713
3714
3715
3716
3717
3718
3719
3720
3721
3722
3723
3724
3725
3726
3727
3728
3729
3730
3731
3732
3733
3734
3735
3736
3737
3738
3739
3740
3741
3742
3743
3744
3745
3746
3747
3748
3749
3750
3751
3752
3753
3754
3755
3756


5218
5219
5220
5221
5222
5223
5224
5225
5226
5227
5228
5229
5230
5231
5232
5233
5234
5235
5236
5237
5238
5239
5240
5241
5242
5243
5244
5245
5246
5247
5248
5249
5250
5251
5252
5253
5254
5255
5256
5257
5258
5259
5260
5261
5262
5263
5264
5265
5266
5267
5268
5269
5270
5271
5272
5273
5274
5275
5276
5277
5278
5279
5280
5281
5282
5283
5284
5285
5286
5287
5288
5289
5290
5291
5292
5293
5294
5295
5296
5297
5298
5299
5300
5301
5302
5303
5304
5305
5306
5307
5308
5309
5310
5311
5312
5313
5314
5315
5316
5317
5318
5319
5320
5321
5322
5323
5324
5325
5326
5327
5328
5329
5330
5331
5332
5333
5334
5335
5336
5337
5338
5339
5340
5341
5342
5343
5344
5345
5346
5347
5348
5349
5350
5351
5352
5353
5354
5355
5356
5357
5358
5359
5360
5361
5362
5363
5364
5365
5366
5367
5368
5369
5370
5371
5372
5373
5374
5375
5376
5377
5378
5379
5380
5381
5382
5383
5384
5385
5386
5387
5388
5389
5390
5391
5392
5393
5394
5395
5396
5397
5398
5399
5400
5401
5402
5403
5404
5405
5406
5407
5408
5409
5410
5411
5412
5413
5414
5415
5416
5417


6878
6879
6880
6881
6882
6883
6884
6885
6886
6887
6888
6889
6890
6891
6892
6893
6894
6895
6896
6897
6898
6899
6900
6901
6902
6903
6904
6905
6906
6907
6908
6909
6910
6911
6912
6913
6914
6915
6916
6917
6918
6919
6920
6921
6922
6923
6924
6925
6926
6927
6928
6929
6930
6931
6932
6933
6934
6935
6936
6937
6938
6939
6940
6941
6942
6943
6944
6945
6946
6947
6948
6949
6950
6951
6952
6953
6954
6955
6956
6957
6958
6959
6960
6961
6962
6963
6964
6965
6966
6967
6968
6969
6970
6971
6972
6973
6974
6975
6976
6977
6978
6979
6980
6981
6982
6983
6984
6985
6986
6987
6988
6989
6990
6991
6992
6993
6994
6995
6996
6997
6998
6999
7000
7001
7002
7003
7004
7005
7006
7007
7008
7009
7010
7011
7012
7013
7014
7015
7016
7017
7018
7019
7020
7021
7022
7023
7024
7025
7026
7027
7028
7029
7030
7031
7032
7033
7034
7035
7036
7037
7038
7039
7040
7041
7042
7043
7044
7045
7046
7047
7048
7049
7050
7051
7052
7053
7054
7055
7056
7057
7058
7059
7060
7061
7062
7063
7064
7065
7066
7067
7068
7069
7070
7071
7072
7073
7074
7075
7076
7077


In [19]:
listing_tsz_df

listing_id  creation_tsz
0    492259062    1537570840
0    464863490    1537299040
0    243657597    1536177505
0    625330096    1535268449
0    639116667    1535242767
0    625280804    1535240898
0    639107951    1535239236
0    243521750    1534568418
0    243518492    1534566013
0    241680506    1533319819
0    257552659    1533075019
0    238573318    1532057419
0    238581690    1530848416
0    238571522    1530848416
0    238569476    1530848415
0    238470269    1530848415
0    238449117    1530848415
0    481091347    1538353840
0    530216099    1539909350
0    464207368    1537980037
0    492512510    1537980036
0    261630013    1537980036
0    233408848    1537980036
0    222447256    1537980035
0    219269069    1537980035
0    213871085    1537980035
0    205732377    1537980035
0    211971680    1537980034
0    208433425    1537980034
0    197510986    1537980034
..         ...           ...
0    561087841    1538392831
0    547288960    1538392831
0    547288344    1538392227
0    547287916    1538392227
0    608640156    1533767424
0    621139667    1539229539
0    637172449    1534540533
0    637171641    1534540319
0    626548409    1530932889
0    626543255    1530930905
0    607935915    1534470615
0    626788971    1531097295
0    612953228    1531097295
0    612950850    1531097295
0    612949472    1531097295
0    612945688    1531097295
0    612943892    1531097295
0    612953922    1531097294
0    607326131    1534222213
0    606122527    1533807014
0    592332424    1533800413
0    589607228    1532761216
0    603388233    1532755815
0    589596776    1532754018
0    603369221    1532746821
0    591085319    1534125083
0    591077633    1538690443
0    577274088    1538690442
0    577276554    1538690442
0    577275168    1538690442

[6819 rows x 2 columns]

In [20]:
# Save the info for future use
listing_tsz_df.to_csv('listing_tsz_df.csv', index=False)